In [1]:

import os
import math
import numpy as np
import numpy.linalg as la
import plotly.graph_objects as go
import plotly.express as ex
from plotly.subplots import make_subplots
import pandas as pd
import time

import json as js
import _pickle as pickle
import bz2
import ray

import torch
import torch.nn as nn
import torchvision
from torch.utils.data import Dataset, TensorDataset
from torch.utils.data import DataLoader
from torch.utils.data.dataset import random_split


In [2]:
def save(file, filename, path):
    with bz2.BZ2File(os.path.join(path, filename+".pbz2"), "w") as f:
        pickle.dump(file, f)
def load(file_path):
    with bz2.BZ2File(file_path, "rb") as f:
        obj = pickle.load(f)
        return obj


In [5]:
a = [1,2,3]
b = a[0::2]
print(b)

[1, 3]


In [3]:
PATH = "C:/Users/Neroro/AppData/LocalLow/DefaultCompany/Procedural Animation"
D1 = "2D_ONE_POS"
D2 = "3D_ONE_POS"
F1 = "dataset1"
F2 = "dataset2"
THREADING = True
CPUs = 24

D = []
# for dname, dirs, files in os.walk("."):
#     for fname in files:
#         filePath = os.path.join(dname, fname)
#         D.append(load(filePath))

D = load("../data/LOCO_R1-default-locomotion.pbz2")



In [5]:
for dname, dirs, files in os.walk(os.path.join(PATH)):
    print(dirs)
    break

['.idea', 'LOCO_R1-default-locomotion', 'LOCO_R1-default-locomotion-large', 'LOCO_R1-default-locomotion-small', 'LOCO_R2-default-locomotion', 'LOCO_R2-default-locomotion-large', 'LOCO_R2-default-locomotion-small', 'LOCO_R3-default-locomotion', 'LOCO_R3-default-locomotion-large', 'LOCO_R3-default-locomotion-small', 'LOCO_R4-default-locomotion', 'LOCO_R4-default-locomotion-large', 'LOCO_R4-default-locomotion-small', 'LOCO_R5-default-locomotion', 'ONE_R1-default-One', 'ONE_R1-default-One-large', 'ONE_R1-default-One-small', 'ONE_R2-default-One', 'ONE_R2-default-One-large', 'ONE_R2-default-One-small', 'ONE_R3-default-One', 'ONE_R3-default-One-large', 'ONE_R3-default-One-small', 'ONE_R4-default-One', 'ONE_R4-default-One-large', 'ONE_R4-default-One-small', 'ONE_R5-default-One', 'TWO_R1-default-Two', 'TWO_R1-default-Two-large', 'TWO_R1-default-Two-small', 'TWO_R2-default-Two', 'TWO_R2-default-Two-large', 'TWO_R2-default-Two-small', 'TWO_R3-default-Two', 'TWO_R3-default-Two-large', 'TWO_R3-defa

In [4]:

x, y = [], []
for d1 in D:
    d1 = pickle.loads(d1)
    frames = []
    ground_truth = []
    for i in range(len(d1["frames"])-1):
        f = d1["frames"][i]
        for jo in f:
            for k,v in jo.items():
                print(k, " : ", v)
        print("-"*70)
    break


key  :  False
isLeft  :  0
chainPos  :  0
geoDistance  :  0.1084238737821579
geoDistanceNormalised  :  1.0
pos  :  [-8.1854520e-14  1.0808906e-01  8.5141538e-03]
rotEuler  :  [5.6161233e-03 8.9836075e+01 2.8040942e+02]
rotQuaternion  :  [-0.45190668  0.54254013 -0.45325482  0.5440502 ]
rotMat  :  [[ 9.9999595e-01  2.8317571e-03  4.2057037e-04]
 [-9.8019838e-05  1.8068084e-01 -9.8354179e-01]
 [ 2.8611124e-03 -9.8353767e-01 -1.8068039e-01]]
inertialObj  :  [[0.12664548 0.         0.        ]
 [0.         0.12664548 0.        ]
 [0.         0.         0.15904315]]
inertial  :  [[ 1.2664551e-01 -1.3404253e-05 -2.4653755e-06]
 [-1.3404253e-05  1.5798551e-01  5.7572871e-03]
 [-2.4653764e-06  5.7572871e-03  1.2770310e-01]]
velocity  :  [0. 0. 0.]
angularVelocity  :  [0. 0. 0.]
linearMomentum  :  [0. 0. 0.]
angularMomentum  :  [0. 0. 0.]
totalMass  :  14.137167930603027
upperLimit  :  [30. 30. 45.]
lowerLimit  :  [-30. -30. -45.]
targetValue  :  [ 3.2555864   0.00842025 -0.16333382]
currentVal

In [11]:
x, y = [], []
for d1 in D:
    d1 = pickle.loads(d1)
    frames = []
    ground_truth = []
    for i in range(len(d1["frames"])-1):
        f = d1["frames"][i]
        f2 = d1["frames"][i+1]
        joints = []
        targets = []
        for jo, jo2 in zip(f,f2):
            # input
            jojo = np.concatenate((jo["pos"],
                                   jo["rotMat"].ravel(),
                                   jo["velocity"],
                                   jo["angularVelocity"],
                                   jo["tGoalPos"],
                                   jo["tGoalDir"],
                                   jo["posCost"],
                                   jo["targetPosition"],
                                   [jo["contact"]]))
            joints.append(jojo)

            # output
            targets.append(np.concatenate((jo2["pos"],
                                           jo2["rotMat"].ravel(),
                                           jo2["posCost"],
                                           )))

        joints = np.vstack(joints).reshape(1,-1)
        targets = np.vstack(targets).reshape(1,-1)

        frames.append(joints)
        ground_truth.append(targets)

    frames = np.vstack(frames)
    frames = normalise(frames)
    ground_truth = np.vstack(ground_truth)

    x.append(frames)
    y.append(ground_truth)

In [6]:
print(len(x))
print(x[0].shape)

print(len(y))
print(y[0].shape)

984
(119, 651)
984
(119, 315)


In [14]:
save(x, "2D_POS_X_Pos-Rot-Vel-AVel-GPos-GDir-Pcost-tPos-C", "")
save(y, "2D_POS_Y_Pos-Rot-Vel-AVel-GPos-GDir-Pcost-tPos-C", "")

In [5]:
x = load("2D_POS_X_Pos-Rot-Vel-AVel-GPos-GDir-Pcost-tPos-C.pbz2")
y = load("2D_POS_Y_Pos-Rot-Vel-AVel-GPos-GDir-Pcost-tPos-C.pbz2")

In [10]:
def normalise(x, axis=0):
    return (x-np.mean(x, axis=axis)) / (np.std(x, axis=axis)+1e-6)


In [ ]:
normalise(frames)


In [8]:
class MLP(nn.Module):
    def __init__(self, input_size, hidden_size=512, output_size=512, keep_prob=0.2):
        super(MLP, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.elu = nn.ELU()
        self.drop = nn.Dropout(keep_prob)
        self.fc2 = nn.Linear(hidden_size, hidden_size)
        self.elu2 = nn.ELU()
        self.drop2 = nn.Dropout(keep_prob)
        self.fc3 = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        return self.fc3(
            self.drop2(
                self.elu2(
                    self.fc2(
                        self.drop(
                            self.elu(
                                self.fc1(x)
                            )
                        )
                    )
                )
            )
        )

class Encoder(nn.Module):
    def __init__(self, input_size, hidden_size=512, output_size=256, keep_prob=0.2):
        super(Encoder, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.elu = nn.ELU()
        self.drop = nn.Dropout(keep_prob)
        self.fc2 = nn.Linear(hidden_size, hidden_size)
        self.elu2 = nn.ELU()
        self.drop2 = nn.Dropout(keep_prob)
        self.fc3 = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        return self.fc3(
            self.drop2(
                self.elu2(
                    self.fc2(
                        self.drop(
                            self.elu(
                                self.fc1(x)
                            )
                        )
                    )
                )
            )
        )

class Decoder(nn.Module):
    def __init__(self, input_size, hidden_size=512, output_size=512, keep_prob=0.2):
        super(Decoder, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.elu = nn.ELU()
        self.drop = nn.Dropout(keep_prob)
        self.fc2 = nn.Linear(hidden_size, hidden_size)
        self.elu2 = nn.ELU()
        self.drop2 = nn.Dropout(keep_prob)
        self.fc3 = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        return self.fc3(
            self.drop2(
                self.elu2(
                    self.fc2(
                        self.drop(
                            self.elu(
                                self.fc1(x)
                            )
                        )
                    )
                )
            )
        )

class EMD(nn.Module):
   def __init__(self, input_size, encoder_size = 512, encoder_output=256, hidden_size=512, output_size=512):
       super(EMD, self).__init__()
       self.encoder = Encoder(input_size, hidden_size=encoder_size, output_size=encoder_output)
       self.mlp = MLP(input_size=encoder_output, hidden_size=hidden_size, output_size=hidden_size)
       self.decoder = Decoder(input_size=hidden_size, hidden_size=encoder_size, output_size=output_size)
   def forward(self, x):
       return self.decoder(self.mlp(self.encoder(x)))


class ED(nn.Module):
   def __init__(self, input_size, encoder_size = 512, encoder_output=256, output_size=512):
       super(ED, self).__init__()
       self.encoder = Encoder(input_size, hidden_size=encoder_size, output_size=encoder_output)
       self.decoder = Decoder(input_size=encoder_output, hidden_size=encoder_size, output_size=output_size)
   def forward(self, x):
       return self.decoder(self.encoder(x))

In [9]:
# Device configuration
print(torch.cuda.is_available())
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)


False
cpu


In [10]:
# Hyper-parameters
input_size = 651
hidden_size = 256
output_size = 315
num_epochs = 100
learning_rate = 0.1
SEED = 2021

# MNIST dataset
x_tensor = torch.from_numpy(np.asarray(x)).float()
y_tensor = torch.from_numpy(np.asarray(y)).float()

dataset = TensorDataset(x_tensor, y_tensor)
N = len(dataset)

In [13]:
train_ratio = int(.7*N)
val_ratio = int(.5 * (N-train_ratio))
test_ratio = int(N-train_ratio-val_ratio)
print(train_ratio, " ", val_ratio, " ", test_ratio)

train_set, val_set, test_set = random_split(dataset, [train_ratio, val_ratio, test_ratio], generator=torch.Generator().manual_seed(SEED))

train_loader = DataLoader(dataset=train_set, batch_size=1)
val_loader = DataLoader(dataset=val_set, batch_size=1)
test_loader = DataLoader(dataset=test_set, batch_size=1)



688   148   148


In [18]:
autoencoder = ED(input_size=input_size, encoder_size=256, encoder_output=128, output_size=input_size)

criterion = nn.MSELoss(reduction="mean")
optimizer = torch.optim.AdamW(autoencoder.parameters(), lr=learning_rate)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=2, gamma=0.1)

total_step = len(train_loader)
i = 0
prev_losses = np.zeros(5)
max_prev_loss = 5
prev_avg_loss = 0
for epoch in range(10):
    for inputs, _ in train_loader:
        inputs = inputs.to(device)

        outputs = autoencoder(inputs)
        loss = criterion(outputs, inputs)

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        i+=1
        if i % 100 == 0:
            print ('Epoch [{}/{}], Step {}, Loss: {:.4f}'
                .format(epoch+1, i, num_epochs, loss.item()))
    # scheduler.step()
    # prev_losses[epoch % 5] = loss.item()
    # if epoch > 10 and epoch % 5 == 0:
    #     if np.mean(prev_losses) / prev_avg_loss > 1.2:
    #         break
    #     else:
    #         prev_avg_loss = np.mean(prev_losses)

print(epoch)
print(i)

Epoch [1/100], Step 100, Loss: 1931.8196
Epoch [1/200], Step 100, Loss: 1509.3717
Epoch [1/300], Step 100, Loss: 1119.9290
Epoch [1/400], Step 100, Loss: 829.6202
Epoch [1/500], Step 100, Loss: 616.0634
Epoch [1/600], Step 100, Loss: 436.8903
Epoch [2/700], Step 100, Loss: 315.1807
Epoch [2/800], Step 100, Loss: 214.9130
Epoch [2/900], Step 100, Loss: 154.0535
Epoch [2/1000], Step 100, Loss: 107.6690
Epoch [2/1100], Step 100, Loss: 74.2226
Epoch [2/1200], Step 100, Loss: 48.9696
Epoch [2/1300], Step 100, Loss: 31.7116
Epoch [3/1400], Step 100, Loss: 22.6331
Epoch [3/1500], Step 100, Loss: 15.0228
Epoch [3/1600], Step 100, Loss: 9.7069
Epoch [3/1700], Step 100, Loss: 7.0999
Epoch [3/1800], Step 100, Loss: 5.1434
Epoch [3/1900], Step 100, Loss: 288.3371
Epoch [3/2000], Step 100, Loss: 4.5824
Epoch [4/2100], Step 100, Loss: 9.1079
Epoch [4/2200], Step 100, Loss: 12.0494
Epoch [4/2300], Step 100, Loss: 36.4754
Epoch [4/2400], Step 100, Loss: 21.0284
Epoch [4/2500], Step 100, Loss: 11.2867


In [19]:
torch.save(autoencoder.state_dict(), 'm_autoencoder.ckpt')

In [ ]:
# model = MLP(input_size, hidden_size, output_size).to(device)
model = EMD(input_size=input_size, encoder_output=128, output_size=output_size)
model.encoder = autoencoder.encoder
model.decoder = autoencoder.decoder


# Loss and optimizer
criterion = nn.MSELoss(reduction="sum")
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=5, gamma=0.1)



# Train the model
total_step = len(train_loader)
i = 0

for epoch in range(num_epochs):
    for inputs, labels in train_loader:
        # Move tensors to the configured device
        inputs = inputs.to(device)
        labels = labels.to(device)

        # Forward pass
        outputs = model(inputs)
        loss = criterion(outputs, labels)

        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
    scheduler.step()

    i+=1
    # if (i+1) % 100 == 0:
    print ('Epoch [{}/{}], Loss: {:.4f}'
       .format(epoch+1, num_epochs, loss.item()))

# Test the model
# In test phase, we don't need to compute gradients (for memory efficiency)
losses = []
with torch.no_grad():
    for inputs, labels in val_loader:
        inputs = inputs.to(device)
        labels = labels.to(device)
        outputs = model(inputs)

        losses.append(criterion(outputs, labels))
# Save the model checkpoint



In [49]:
torch.save(model.state_dict(), 'm_mlp_batch=1.ckpt')

In [50]:
for l in losses:
    print(l.numpy())



281.79236
168.09427
141.26617
239.81529
201.2288
251.419
292.52774
265.49704
109.145035
174.30162
200.40536
137.53061
432.10425
197.66963
210.73825
139.50948
111.28489
273.51382
142.71284
276.90082
93.50858
147.46948
121.629105
249.60558
251.92928
146.60304
171.37364
204.57764
152.05347
262.54697
195.80403
205.51749
108.42576
211.2148
134.85762
184.13632
254.69225
146.34204
208.36546
316.57364
255.2513
204.12866
190.05795
200.22452
219.74574
134.49565
204.82443
250.13303
223.86653
155.37848
231.76076
239.96971
158.54967
180.9454
265.21002
139.1075
119.80133
215.60626
181.41945
241.07431
197.51012
254.95709
193.41852
188.27254
155.96509
214.26334
173.22757
280.83456
325.01218
224.67708
105.48035
132.09737
214.53731
154.87991
106.25681
196.68698
213.4931
258.74542
159.5486
135.3585
171.45006
241.39441
231.46371
149.23936
181.67981
167.07034
173.12245
176.79492
329.00888
186.00262
214.98314
143.96362
232.0621
247.16046
174.82596
150.23953
332.66327
169.89743
209.01787
156.18233
327.1604
1

In [71]:
xs = []
ys = []
xp = []
with torch.no_grad():
    for x_sample, y_sample in train_loader:
        xs = x_sample
        ys = y_sample
        start = time.time()
        xp = model(x_sample)
        print(time.time()-start)
        break
    xss = xs.numpy()
    yss = ys.numpy()
    xpp = xp.numpy()

0.002001047134399414


In [77]:
print(yss.shape)

original = yss[0]
predicted = xpp[0]

d1 = {"data" : [{"joints": o.tolist()} for o in original]}
d2 = {"data": [{"joints": o.tolist()} for o in predicted]}

with open("original_clip.json", "w") as f:
    js.dump(d1, f)
with open("predicted_clip.json", "w") as f:
    js.dump(d2, f)


(1, 119, 63)


In [80]:
for dname, dirs, files in os.walk(os.path.join(PATH, D1)):
    for fname in files:
        filePath = os.path.join(dname, fname)
        raw = js.load(open(filePath, "r"))
        break
    break


In [84]:
for i in range(119):
    for j in range(21):
        raw["frames"][i]["joints"][j]["x"]["TargetValue"] = float(original[i,j*3])
        raw["frames"][i]["joints"][j]["y"]["TargetValue"] = float(original[i,j*3+1])
        raw["frames"][i]["joints"][j]["z"]["TargetValue"] = float(original[i,j*3+2])

with open("original_clip.json", "w") as f:
    js.dump(raw, f)

In [85]:
for i in range(119):
    for j in range(21):
        raw["frames"][i]["joints"][j]["x"]["TargetValue"] = float(predicted[i,j*3])
        raw["frames"][i]["joints"][j]["y"]["TargetValue"] = float(predicted[i,j*3+1])
        raw["frames"][i]["joints"][j]["z"]["TargetValue"] = float(predicted[i,j*3+2])

with open("predicted_clip.json", "w") as f:
    js.dump(raw, f)
